# Capstone Project - The Battle of the Neighborhoods (Week 1)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a Hot Pot restaurant . Specifically, this report will be targeted to stakeholders interested in opening an **Hot Pot Restaurant** in **ChengDu**, China.

Since there are lots of Hot Pot restaurant in ChengDu we will try to detect **locations that are not already crowded with restaurant**. We are also particularly interested in **areas with no Hot Pot restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing hotel in the neighborhood (any type of hotel)
* number of and distance to Hot Pot restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* number of hotel and their type and location in every neighborhood will be obtained using **Baidu API**
* coordinate of ChengDu center will be obtained using ***Baidu API*** of well known ChengDu location (Tianfu Square)
* maps of these hotels will by displayed using **matplotlib**

In [1]:
import numpy as np # library to handle data in a vectorized manner
import requests

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

#import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


####  Let's first find the latitude & longitude of Tianfu Square,ChengDu city center, using specific, well known BaiDu API.

define token of baidu maps

In [2]:
#token = 'z2vyiZEgrM2E3j37VfwqapGcs2iguIgO'
#token = 'kMGC86ir7BY9io9fvxEA8ARHfMk6mNKS'
token = 'z2vyiZEgrM2E3j37VfwqapGcs2iguIgO'
#token = 'wGhALH6ylW9azwwmQybUEGyjICv16cuP' #vip

In [3]:
#http://api.map.baidu.com/geocoding/v3/?address=北京市海淀区上地十街10号&output=json&ak=您的ak&callback=showLocation //GET请求
adress='四川省成都市天府广场'
url = 'http://api.map.baidu.com/geocoding/v3/?address='+adress+'&output=json&ak='+token#+'&callback=showLocation'
#print(url)
r = requests.get(url)
#print(r)
#r = requests.post(url)
response_dict = r.json()
#print(response_dict)
results =  response_dict["result"]
coordinate = results['location']
lng=coordinate['lng']
lat=coordinate['lat']
print('coordinate=lng:'+str(lng)+' lat:'+str(lat))

coordinate=lng:104.07236251004944 lat:30.663315899548742


#### define function get_coordinates using baidu api

In [4]:
#http://api.map.baidu.com/place/v2/search?query=ATM机&tag=银行&region=北京&output=json&ak=您的ak //GET请求
address='科技馆'
def get_coordinates(token,address):
    try:
        url = 'http://api.map.baidu.com/place/v2/search?query='+address+'&region=成都&output=json&ak='+token#+'&callback=showLocation'
        print(url)
        r = requests.get(url)
        #print(r)
        #r = requests.post(url)
        response_dict = r.json()
        #print(response_dict)
        results = response_dict['results']
        results_first =  results[0] #get address details fet the first row
        #print(results_first)
        coordinate = results_first['location']
        province = results_first['province']
        city = results_first['city']
        area = results_first['area']
        addressdetails = results_first['address']
        lng=coordinate['lng']
        lat=coordinate['lat']
        return [lat, lng]
    except:
        return[None,None]        
chengdu_center = get_coordinates(token,address)
print('Coordinate of {}: {}'.format(address, chengdu_center))

http://api.map.baidu.com/place/v2/search?query=科技馆&region=成都&output=json&ak=z2vyiZEgrM2E3j37VfwqapGcs2iguIgO
Coordinate of 科技馆: [30.665891, 104.072219]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Alexanderplatz. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [5]:
CLIENT_ID = 'VP0QNMVOG5IXARGPH4RTNX0UT3TJSIDEUD5CMESELQQ5KXUT' # your Foursquare ID
CLIENT_SECRET = 'OP1FGHT3CK5GMKNVJ0DOVBT0BP3WREE0NAAYRXSOONPZMADS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: VP0QNMVOG5IXARGPH4RTNX0UT3TJSIDEUD5CMESELQQ5KXUT
CLIENT_SECRET:OP1FGHT3CK5GMKNVJ0DOVBT0BP3WREE0NAAYRXSOONPZMADS


<a>It is used for the mutual conversion of baidu coordinate system (bd-09), Mars coordinate system (GBS coordinate system, gcj02), and WGS84 coordinate system, and provides the conversion function of Chinese address to coordinate. It only USES Python standard module, without any other dependence.></a><br>
<a>（**In Chinese**：定义用于百度坐标系(bd-09)、火星坐标系(国测局坐标系、gcj02)、WGS84坐标系的相互转换，并提供中文地址到坐标的转换功能，仅使用Python标准模块，无其他依赖。
中文地址到坐标转换使用高德地图API，需要申请API KEY）</a>

In [6]:
import json
import urllib
import math

x_pi = 3.14159265358979324 * 3000.0 / 180.0
pi = 3.1415926535897932384626  # π
a = 6378245.0  # 长半轴
ee = 0.00669342162296594323  # 偏心率平方


class Geocoding:
    def __init__(self, api_key):
        self.api_key = api_key

    def geocode(self, address):
        """
        利用高德geocoding服务解析地址获取位置坐标
        :param address:需要解析的地址
        :return:
        """
        geocoding = {'s': 'rsv3',
                     'key': self.api_key,
                     'city': '全国',
                     'address': address}
        geocoding = urllib.parse.urlencode(geocoding)
        ret = urllib.request.urlopen("%s?%s" % ("http://restapi.amap.com/v3/geocode/geo", geocoding))

        if ret.getcode() == 200:
            res = ret.read()
            json_obj = json.loads(res)
            if json_obj['status'] == '1' and int(json_obj['count']) >= 1:
                geocodes = json_obj['geocodes'][0]
                lng = float(geocodes.get('location').split(',')[0])
                lat = float(geocodes.get('location').split(',')[1])
                return [lng, lat]
            else:
                return None
        else:
            return None


def gcj02_to_bd09(lng, lat):
    """
    火星坐标系(GCJ-02)转百度坐标系(BD-09)
    谷歌、高德——>百度
    :param lng:火星坐标经度
    :param lat:火星坐标纬度
    :return:
    """
    z = math.sqrt(lng * lng + lat * lat) + 0.00002 * math.sin(lat * x_pi)
    theta = math.atan2(lat, lng) + 0.000003 * math.cos(lng * x_pi)
    bd_lng = z * math.cos(theta) + 0.0065
    bd_lat = z * math.sin(theta) + 0.006
    return [bd_lng, bd_lat]


def bd09_to_gcj02(bd_lon, bd_lat):
    """
    百度坐标系(BD-09)转火星坐标系(GCJ-02)
    百度——>谷歌、高德
    :param bd_lat:百度坐标纬度
    :param bd_lon:百度坐标经度
    :return:转换后的坐标列表形式
    """
    x = bd_lon - 0.0065
    y = bd_lat - 0.006
    z = math.sqrt(x * x + y * y) - 0.00002 * math.sin(y * x_pi)
    theta = math.atan2(y, x) - 0.000003 * math.cos(x * x_pi)
    gg_lng = z * math.cos(theta)
    gg_lat = z * math.sin(theta)
    return [gg_lng, gg_lat]


def wgs84_to_gcj02(lng, lat):
    """
    WGS84转GCJ02(火星坐标系)
    :param lng:WGS84坐标系的经度
    :param lat:WGS84坐标系的纬度
    :return:
    """
    if out_of_china(lng, lat):  # 判断是否在国内
        return [lng, lat]
    dlat = _transformlat(lng - 105.0, lat - 35.0)
    dlng = _transformlng(lng - 105.0, lat - 35.0)
    radlat = lat / 180.0 * pi
    magic = math.sin(radlat)
    magic = 1 - ee * magic * magic
    sqrtmagic = math.sqrt(magic)
    dlat = (dlat * 180.0) / ((a * (1 - ee)) / (magic * sqrtmagic) * pi)
    dlng = (dlng * 180.0) / (a / sqrtmagic * math.cos(radlat) * pi)
    mglat = lat + dlat
    mglng = lng + dlng
    return [mglng, mglat]


def gcj02_to_wgs84(lng, lat):
    """
    GCJ02(火星坐标系)转GPS84
    :param lng:火星坐标系的经度
    :param lat:火星坐标系纬度
    :return:
    """
    if out_of_china(lng, lat):
        return [lng, lat]
    dlat = _transformlat(lng - 105.0, lat - 35.0)
    dlng = _transformlng(lng - 105.0, lat - 35.0)
    radlat = lat / 180.0 * pi
    magic = math.sin(radlat)
    magic = 1 - ee * magic * magic
    sqrtmagic = math.sqrt(magic)
    dlat = (dlat * 180.0) / ((a * (1 - ee)) / (magic * sqrtmagic) * pi)
    dlng = (dlng * 180.0) / (a / sqrtmagic * math.cos(radlat) * pi)
    mglat = lat + dlat
    mglng = lng + dlng
    return [lng * 2 - mglng, lat * 2 - mglat]


def bd09_to_wgs84(bd_lon, bd_lat):
    lon, lat = bd09_to_gcj02(bd_lon, bd_lat)
    return gcj02_to_wgs84(lon, lat)


def wgs84_to_bd09(lon, lat):
    lon, lat = wgs84_to_gcj02(lon, lat)
    return gcj02_to_bd09(lon, lat)


def _transformlat(lng, lat):
    ret = -100.0 + 2.0 * lng + 3.0 * lat + 0.2 * lat * lat + \
          0.1 * lng * lat + 0.2 * math.sqrt(math.fabs(lng))
    ret += (20.0 * math.sin(6.0 * lng * pi) + 20.0 *
            math.sin(2.0 * lng * pi)) * 2.0 / 3.0
    ret += (20.0 * math.sin(lat * pi) + 40.0 *
            math.sin(lat / 3.0 * pi)) * 2.0 / 3.0
    ret += (160.0 * math.sin(lat / 12.0 * pi) + 320 *
            math.sin(lat * pi / 30.0)) * 2.0 / 3.0
    return ret


def _transformlng(lng, lat):
    ret = 300.0 + lng + 2.0 * lat + 0.1 * lng * lng + \
          0.1 * lng * lat + 0.1 * math.sqrt(math.fabs(lng))
    ret += (20.0 * math.sin(6.0 * lng * pi) + 20.0 *
            math.sin(2.0 * lng * pi)) * 2.0 / 3.0
    ret += (20.0 * math.sin(lng * pi) + 40.0 *
            math.sin(lng / 3.0 * pi)) * 2.0 / 3.0
    ret += (150.0 * math.sin(lng / 12.0 * pi) + 300.0 *
            math.sin(lng / 30.0 * pi)) * 2.0 / 3.0
    return ret


def out_of_china(lng, lat):
    """
    判断是否在国内，不在国内不做偏移
    :param lng:
    :param lat:
    :return:
    """
    return not (lng > 73.66 and lng < 135.05 and lat > 3.86 and lat < 53.55)


if __name__ == '__main__':
    lng = 128.543
    lat = 37.065
    result1 = gcj02_to_bd09(lng, lat)
    result2 = bd09_to_gcj02(lng, lat)
    result3 = wgs84_to_gcj02(lng, lat)
    result4 = gcj02_to_wgs84(lng, lat)
    result5 = bd09_to_wgs84(lng, lat)
    result6 = wgs84_to_bd09(lng, lat)

    g = Geocoding('2f041565470798cca68fe8c2e6fa45c9')  # 这里填写你的高德api的key
    result7 = g.geocode('四川省成都市科技馆')
    print (result1, result2, result3, result4, result5, result6, result7)

[128.54944656269413, 37.07113427883019] [128.5365893261212, 37.058754503281534] [128.54820547949757, 37.065651049489816] [128.53779452050244, 37.06434895051018] [128.53136876750008, 37.0580926428705] [128.55468192918485, 37.07168344938498] None


In [7]:
lng = 128.543
lat = 37.065
result1 = gcj02_to_bd09(lng, lat)#火星坐标系->百度坐标系
result2 = bd09_to_gcj02(lng, lat)#百度坐标系->火星坐标系
result3 = wgs84_to_gcj02(lng, lat)#WGS84坐标系->火星坐标系
result4 = gcj02_to_wgs84(lng, lat)#火星坐标系->WGS84坐标系
result5 = bd09_to_wgs84(lng, lat)#百度坐标系->WGS84坐标系
result6 = wgs84_to_bd09(lng, lat)#WGS84坐标系->百度坐标系
#中文地址到火星坐标系,需要高德地图API Key
g = Geocoding('2f041565470798cca68fe8c2e6fa45c9')  # 这里填写你的高德Api_Key
result7 = g.geocode('北京市朝阳区朝阳公园')
print(result1, result2, result3, result4, result5, result6, result7)

[128.54944656269413, 37.07113427883019] [128.5365893261212, 37.058754503281534] [128.54820547949757, 37.065651049489816] [128.53779452050244, 37.06434895051018] [128.53136876750008, 37.0580926428705] [128.55468192918485, 37.07168344938498] None


In [49]:
#!pip install shapely
#conda install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

# zone  UTM zone 成都在 48 
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=48, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=48, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('ChengDu center longitude={}, latitude={}'.format(chengdu_center[1], chengdu_center[0]))
x, y = lonlat_to_xy(chengdu_center[1], chengdu_center[0])
print('ChengDu center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('ChengDu center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
ChengDu center longitude=104.072219, latitude=30.665891
ChengDu center UTM X=411119.22526361543, Y=3392942.26822334
ChengDu center longitude=104.072219, latitude=30.665891


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [50]:
chengdu_center_wgs84  = bd09_to_wgs84(chengdu_center[1], chengdu_center[0]) #转换为wgs84计算
chengdu_center_x, chengdu_center_y = lonlat_to_xy(chengdu_center_wgs84[0], chengdu_center_wgs84[1]) # City center in Cartesian coordinates
print(chengdu_center)
print('chengdu_center_x, chengdu_center_y:'+str(chengdu_center_x)+','+str(chengdu_center_y))
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = chengdu_center_x - 16000
x_step = 1600
y_min = chengdu_center_y - 16000 - (int(21/k)*k*1600 - 32000)/2
y_step = 1600 * k 

print('min:'+str(x_min)+','+str(y_min))

latitudes = [] ##wgs84计算
longitudes = [] ##wgs84计算
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 800 if i%2==0 else 0
    for j in range(0, 33):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(chengdu_center_x,chengdu_center_y, x, y)
        if (distance_from_center <= 16001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)
           # print('x,y'+str(x)+','+str(y)+'   lan,lat'+str(lon)+','+str(lat))

print(len(latitudes), 'candidate neighborhood centers generated.')
print(latitudes[0],longitudes[0])

[30.665891, 104.072219]
chengdu_center_x, chengdu_center_y:410254.85318447585,3392545.033692162
min:394254.85318447585,3375917.3459395007
364 candidate neighborhood centers generated.
30.524350825365996 104.01452774082877


In [26]:
#chengdu_center_new using wgs84计算
chengdu_center_new=[chengdu_center_wgs84[1], chengdu_center_wgs84[0]]
print(chengdu_center_new)
print(chengdu_center)

[30.66224223020602, 104.06323184726676]
[30.665891, 104.072219]


In [52]:
#!pip install folium
import folium
map_chengdu = folium.Map(location=[chengdu_center_wgs84[1],chengdu_center_wgs84[0]], zoom_start=13)
folium.Marker([chengdu_center_wgs84[1],chengdu_center_wgs84[0]], popup='ChengDu,China').add_to(map_chengdu)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=800, color='blue', fill=False).add_to(map_chengdu)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_chengdu

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Tianfu Square

Let's now use BaiDu Maps API to get approximate addresses of those locations.

In [53]:
def get_address(latitude, longitude,coordtype,ret_coordtype):
    try:
        token = "z2vyiZEgrM2E3j37VfwqapGcs2iguIgO"
        url = 'http://api.map.baidu.com/reverse_geocoding/v3/?ak='+token+'&output=json&coordtype='+coordtype+'&ret_coordtype='+ret_coordtype+'&location='+str(latitude)+','+str(longitude)
        r = requests.get(url)
        response_dict = r.json()
        results =  response_dict["result"]
        #print(results)
        formatted_address =  results['formatted_address']
        business =  results['business']
        return business,formatted_address
    except:
        return None
    
#坐标的类型，目前支持的坐标类型包括：bd09ll（百度经纬度坐标）、bd09mc（百度米制坐标）、gcj02ll（国测局经纬度坐标，仅限中国）、wgs84ll（ GPS经纬度）
coordtype = 'bd09ll' 
ret_coordtype = 'wgs84ll' 
addr,formatted_address = get_address('30.665891','104.072219',coordtype = 'bd09ll',ret_coordtype = 'wgs84ll' )
print(addr)
print(formatted_address)


天府广场,人民中路,西华门
四川省成都市青羊区人民中路一段16号


In [54]:
print('Obtaining location addresses: ', end='')
addresses = []
formatted_address = []
for lat, lon in zip(latitudes, longitudes):
    addr,formatted_addr = get_address(lat, lon ,coordtype = 'wgs84ll',ret_coordtype = 'wgs84ll' )
    if address is None:
        address = 'NO ADDRESS'
    addresses.append(addr)
    formatted_address.append(formatted_addr)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


Looking good. Let's now place all this into a Pandas dataframe.

In [55]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'formatted_address': formatted_address,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(100)

Address         formatted_address   Latitude   Longitude  \
0                                 四川省成都市双流区  30.524351  104.014528   
1                            四川省成都市双流区锦江路四段  30.524476  104.031203   
2                            四川省成都市双流区滨河路2段  30.524599  104.047878   
3                            四川省成都市双流区伏龙路1段  30.524720  104.064554   
4                             四川省成都市双流区新通大道  30.524838  104.081229   
5                             四川省成都市双流区新通大道  30.524955  104.097905   
6                              四川省成都市双流区双简路  30.525069  104.114581   
7                        四川省成都市双流区长城路2段-59号  30.536661  103.989386   
8                                 四川省成都市双流区  30.536789  104.006063   
9                              四川省成都市双流区荣店路  30.536916  104.022740   
10                                四川省成都市武侯区  30.537040  104.039418   
11                             四川省成都市双流区吉泰路  30.537162  104.056095   
12                       四川省成都市双流区G213(锦韵路)  30.537281  104.072773   
13                           四川省成都市双流区应龙北二路  30.537399  104.089451   
14                             四川省成都市双流区安和路  30.537515  104.106128   
15                                四川省成都市双流区  30.537628  104.122806   
16                             四川省成都市双流区新三路  30.537739  104.139484   
17            航空港              四川省成都市双流区会缘路  30.548966  103.964237   
18         文星,航空港             四川省成都市双流区文星正街  30.549098  103.980917   
19             文星            四川省成都市双流区西航港新街  30.549227  103.997596   
20             白家      四川省成都市双流区G93(成渝环线高速)  30.549355  104.014275   
21             白家             四川省成都市武侯区天府三街  30.549480  104.030955   
22           世豪广场             四川省成都市武侯区天府三街  30.549603  104.047634   
23       新会展中心,中和          四川省成都市武侯区天府三街19号  30.549724  104.064314   
24       中和,新会展中心           四川省成都市双流区中和大道二段  30.549843  104.080994   
25             中和             四川省成都市双流区中和二街  30.549959  104.097674   
26             中和                 四川省成都市双流区  30.550074  104.114354   
27                             四川省成都市双流区跳墩路  30.550186  104.131034   
28                         四川省成都市双流区成都新机场高速  30.550296  104.147714   
29                         四川省成都市龙泉驿区经开区南五路  30.550405  104.164395   
30         航空港,文星            四川省成都市双流区京昆线辅路  30.561402  103.955764   
31         航空港,文星              四川省成都市双流区口岸路  30.561534  103.972445   
32         航空港,白家            四川省成都市双流区长城路一段  30.561665  103.989127   
33         白家,航空港           四川省成都市双流区黄河中路一段  30.561793  104.005808   
34  白家,航空港,石羊/石羊场       四川省成都市双流区G5(成渝环线高速)  30.561920  104.022490   
35         石羊/石羊场             四川省成都市武侯区富华北路  30.562044  104.039171   
36          新会展中心             四川省成都市武侯区吉庆一路  30.562166  104.055853   
37          新会展中心      四川省成都市武侯区世纪城路198号附1号  30.562286  104.072535   
38       中和,新会展中心              四川省成都市双流区朝阳路  30.562404  104.089217   
39             中和            四川省成都市双流区康和东一街  30.562519  104.105899   
40            成龙路              四川省成都市锦江区庙山巷  30.562633  104.122581   
41            成龙路           四川省成都市双流区新富街334  30.562744  104.139264   
42         大面,成龙路             四川省成都市龙泉驿区黉柏路  30.562853  104.155946   
43     大面,成龙路,世茂城          四川省成都市龙泉驿区经开区南二路  30.562960  104.172629   
44         航空港,文星                 四川省成都市双流区  30.573836  103.947288   
45         航空港,文星            四川省成都市双流区机场东一路  30.573970  103.963972   
46         航空港,文星           四川省成都市双流区机场路常乐段  30.574102  103.980655   
47         航空港,白家      四川省成都市双流区黄河中路2段-137号  30.574231  103.997339   
48  白家,航空港,石羊/石羊场            四川省成都市双流区京昆线辅路  30.574359  104.014022   
49  石羊/石羊场,白家,航空港              四川省成都市双流区黄荆路  30.574484  104.030706   
50         石羊/石羊场             四川省成都市武侯区锦悦西路  30.574607  104.047390   
51          新会展中心            四川省成都市武侯区锦悦西路2  30.574728  104.064074   
52       中和,新会展中心                 四川省成都市锦江区  30.574847  104.080758   
53             中和              四川省成都市锦江区康达路  30.574964  104.097442   
54             中和              四川省成都市锦江区琉新路  30.575078  104.114127   
55            成龙路              四川省成都市锦江区时蔬路  30.575191  104.130811   
56         成龙路,大面   

...and let's now save/persist this data into local file.

In [56]:
df_locations.to_pickle('locations.pkl')

Now that we have our location candidates, let's use BaiDu API to get info on restaurants in each neighborhood.

In [57]:
token = 'n6iyUTUq8aUBflLOgfz7wZpEjzccNagj'

In [58]:
import time

def get_venues_near_location(token,lat,lng,radius,limit,query_type,maxlimit,coordtype,ret_coordtype):
    try:
        #print('lat+lng'+str(lat)+','+str(lng))
        venues_all=[]
        if maxlimit%limit == 0:
            max_pageadd = 0
        else:
            max_pageadd = 1
        max_pagenum=int(maxlimit/limit) + max_pageadd
        #print(max_pagenum)
        
        page_num = 1
        for i in range(max_pagenum):
            # fetch each page data
            venues=[]
            url = 'http://api.map.baidu.com/place/v2/search?query='+query_type+'&coordtype='+coordtype+'&ret_coordtype='+ret_coordtype+'&location='+str(lat)+','+str(lng)+'&radius='+str(radius)+'&radius_limit=true&scope=2&ret_coordtype=wgs84ll&output=json&page_size='+str(limit)+'&page_num='+str(page_num)+'&ak='+token#+'&callback=showLocation'
            #print(url)
            
            #print(time.ctime())
            time.sleep( 1 ) # 防止达到百度最大并发量
            #print(time.ctime())
            
            r = requests.get(url)
            response_dict = r.json()
            #print(response_dict)
            results = response_dict['results'] 
            #print(results)            
            #print(len(results))
            if len(results)==0:
                break
            else:
                '''
                venues = [(item['uid'],
                       item['name'],
                       item['detail_info']['type'],
                       item['detail_info']['tag'],
                       (item['location']['lat'], item['location']['lng']),
                       item['address'],
                       item['detail_info']['distance'] 
                      ) for item in results]
                '''
                venues=[]
                for item in results:
                    if ('uid' in item):
                        uid=item['uid']
                    else:
                        uid=''
                    if ('name' in item):
                        name=item['name'] 
                    else:
                        name=''   
                    if ('type' in item['detail_info']):
                        place_type=item['detail_info']['type']
                    else:
                        place_type=''
                    if ('tag' in item['detail_info']):
                        place_tag=item['detail_info']['tag']
                    else:
                        place_tag=''
                    place_cor=(item['location']['lat'], item['location']['lng'])
                    if ('address' in item):
                        address=item['address']
                    else:
                        address=''
                    if ('distance' in item['detail_info']): 
                        distance = item['detail_info']['distance'] 
                    else:
                        distance=80000000
                    venues_per=[(uid,name,place_type,place_tag,place_cor,address,distance)]
                    #print(venues_per)
                    if (place_tag=='美食;中餐厅' or place_tag=='美食;外国餐厅'):# or place_tag=='美食;小吃快餐店'):
                        venues=venues+venues_per
            venues_all = venues_all+venues
            page_num=page_num+1
        #print(len(venues_all))
        return venues_all
    #except:
    #    venues_all = []
    except IndexError as e:
        venues_all = []
        print(e)
        return venues_all 

radius=408# limit of distance from search center
limit=20   # limit of each fetch page
maxlimit=100  # limit of max num of seach
query_type='美食'
print(chengdu_center)
#print(chengdu_center_new)
print(chengdu_center_wgs84)
#坐标的类型，目前支持的坐标类型包括：bd09ll（百度经纬度坐标）、bd09mc（百度米制坐标）、gcj02ll（国测局经纬度坐标，仅限中国）、wgs84ll（ GPS经纬度）
#result_venu=get_venues_near_location(token,chengdu_center[0],chengdu_center[1],radius,limit,query_type,maxlimit,coordtype='bd09ll',ret_coordtype='wgs84ll')
result_venu = get_venues_near_location(token,30.649877,104.019099,radius,limit,query_type,maxlimit,coordtype='wgs84ll',ret_coordtype='wgs84ll')
print(len(result_venu))
result_venu
#30.709213	104.016824
#30.649877	104.019099

[30.665891, 104.072219]
[104.06323184726676, 30.66224223020602]
9


[('c879fa019d795d53c809f0ae',
  '大蓉和酒楼(外双楠店)',
  'cater',
  '美食;中餐厅',
  (30.647187, 104.018408),
  '栖霞路46号附10号',
  306),
 ('f03c176a90424462afee7a25',
  '珊月虾(鹭岛店)',
  'cater',
  '美食;中餐厅',
  (30.652118, 104.019017),
  '鹭岛步行街鹭岛路33号',
  249),
 ('614a892209f6ba90d8d891e0',
  '大足特色臊子面(逸都路店)',
  'cater',
  '美食;中餐厅',
  (30.650945, 104.022817),
  '成都市武侯区双安东巷1号附107号',
  374),
 ('27bebb609977fcde2b06ced0',
  '老土鸭',
  'cater',
  '美食;中餐厅',
  (30.650081, 104.022444),
  '双安北巷1号附4',
  320),
 ('b7f518b28afa5e9b5d0d0239',
  '宽窖罐罐串串ATTKTV',
  'cater',
  '美食;中餐厅',
  (30.650639, 104.020489),
  '龙华南路46号',
  157),
 ('2c2af152dd18acd430f71d03',
  '洪雅土鸡',
  'cater',
  '美食;中餐厅',
  (30.649928, 104.022637),
  '四川省成都市武侯区双安东巷1号-附141附近',
  338),
 ('f167e5fd11b1f85a86420e07',
  '蜀南土黑猪',
  'cater',
  '美食;中餐厅',
  (30.649928, 104.022637),
  '四川省成都市武侯区双安东巷1-129号附近',
  338),
 ('f8ace1b2d16947f1871541bc',
  '蜀饺香',
  'cater',
  '美食;中餐厅',
  (30.649128, 104.022673),
  '四川省成都市武侯区双安东巷2-28号附近',
  351),
 ('565396f81991f596f7eafc

In [59]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants
import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    hot_pot_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(token,lat, lon,radius=800,limit=20,query_type='美食',maxlimit=200,coordtype='wgs84ll',ret_coordtype='wgs84ll')
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_type = venue[2]
            venue_tag =venue[3]
            venue_latlon = venue[4]
            venue_address = venue[5]
            venue_distance = venue[6]
            # 判断是否是餐饮
            if '美食' in venue_tag:
                is_res = True
            else:
                is_res = False
            #判断是否是火锅店
            if '火锅' in venue_name:
                is_hot_pot = True
            else:
                is_hot_pot = False 
            #-----------------------------------------
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_hot_pot, x, y,venue_type,venue_tag)
                if venue_distance<=800:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_hot_pot:
                    hot_pot_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, hot_pot_restaurants, location_restaurants

#restaurants, hot_pot_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)

# Try to load from local file system in case we did this before
restaurants = {}
hot_pot_restaurants = {}
location_restaurants = []
loaded = False

"""
try:
    with open('restaurants_150.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('hot_pot_restaurants_150.pkl', 'rb') as f:
        hot_pot_restaurants = pickle.load(f)
    with open('location_restaurants_150.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass
"""
# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, hot_pot_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_500.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('hot_pot_restaurants_500.pkl', 'wb') as f:
        pickle.dump(hot_pot_restaurants, f)
    with open('location_restaurants_500.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
       

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [60]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of hot_pot_restaurants:', len(hot_pot_restaurants))
print('Percentage of Hot Pot restaurants: {:.2f}%'.format(len(hot_pot_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 7919
Total number of hot_pot_restaurants: 492
Percentage of Hot Pot restaurants: 6.21%
Average number of restaurants in neighborhood: 21.755494505494507


In [61]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('8744063bcaf78a5a6fc02cd8', '特色铁板炒饭', 30.524928, 104.007429, '四川省成都市双流区光电大道四川现代职业学院东100米', 682, False, 404774.337404208, 3377372.923832404, 'cater', '美食;中餐厅')
('521e05dc9c4c208517c8f660', '咬球餐吧', 30.525308, 104.007435, '四川省成都市双流区黄土埝路', 687, False, 404775.2836528329, 3377415.032306671, 'cater', '美食;中餐厅')
('b4bf00d79fc906982dfaa746', '舌尖冒菜(华创路店)', 30.524985, 104.006463, '西航港街道九龙湖社区华创路东三巷71号', 775, False, 404681.71203493787, 3377380.056834663, 'cater', '美食;中餐厅')
('fcfd368768699e76e9f853c2', '疯哥香卤饭店', 30.525652, 104.021921, '华阳镇街道双华路四段三江悦府5栋1单元', 722, False, 406165.43865991296, 3377441.0151004065, 'cater', '美食;中餐厅')
('c111231a93f2a614c27da28a', '玉记冒菜(世纪华联购物中心店)', 30.524928, 104.006483, '华创路68号', 773, False, 404683.5752538844, 3377373.722901071, 'cater', '美食;中餐厅')
('6042af06b70c31147f29bd72', '双记糯香居', 30.524928, 104.006483, '四川省成都市双流区华创路', 773, False, 404683.5752538844, 3377373.722901071, 'cater', '美食;中餐厅')
('99b308c4c97bf58ee8e582d7', '宜宾饭店'

In [62]:
print('List of Hot Pot restaurants')
print('---------------------------')
for r in list(hot_pot_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(hot_pot_restaurants))

List of Hot Pot restaurants
---------------------------
('01d50a740b94988e4e5547be', '川渝故事市井火锅', 30.52055, 104.049571, '成都市双流区协和下街127号', 478, True, 408813.46987556614, 3376852.910601474, 'cater', '美食;中餐厅')
('92fe80c59cfda86d2a02e1d1', '黄桷树自助餐火锅(华阳店)', 30.518036, 104.067367, '成都市双流区龙灯山路一段3', 790, True, 410518.6335347871, 3376560.0481905104, 'cater', '美食;中餐厅')
('a8e8bed849108cd507026f45', '666老火锅', 30.519726, 104.066182, '四川省成都市双流区安公路3段-416', 576, True, 410406.48421959596, 3376748.281377232, 'cater', '美食;中餐厅')
('c758ccafa135c7dc725e80e9', '成都市很好吃的火锅粉', 30.517734, 104.065253, '双流区华阳街道富民路一段258号1层', 779, True, 410315.519975823, 3376528.257992364, 'cater', '美食;中餐厅')
('f775bdb406afd70b30169bb3', '野菌排骨汤火锅', 30.526196, 104.061058, '四川省成都市双流区安公路二段426', 372, True, 409920.8181023023, 3377469.394749195, 'cater', '美食;中餐厅')
('a2ac04e4abb0560b87154165', '拾八碗市井火锅', 30.52639, 104.070113, '伏龙路新希望大道二段4号', 563, True, 410789.7413340425, 3377483.697581715, 'cater', '美食;中餐厅')
('e6749b2d388b67f9740269b4', '颜耗儿

In [63]:
print('Restaurants around location')
print('---------------------------')
for i in range(200, 210):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 201: 百味记小郡肝砂罐串串(百寿路店), 陈婆婆珍藏菜(西安南路店), 玖玖香冒菜(中医学院店), 学府酒楼, 荆山蓬门, 土豆疯了(白果林店), 蜀江鱼火锅(中新路店), 天天冒菜(青羊北路店)
Restaurants around location 202: 眉州东坡酒楼(宽窄巷子店), 天趣·紫园, 金熊猫餐厅(宽巷子店), 竹菴文化院子, 蜀上火锅(宽窄巷子店), 豪客来(宁夏街餐厅), 必胜客(骡马市餐厅), 尽膳河鲜馆(窄巷子店)
Restaurants around location 203: 文殊坊美食街, 和席酒楼(人民中路店), 文殊院香园·福慧厅, 谷焱大牛炭火烧肉, 蒋姐蹄花, 源味炖品川菜馆(大墙西街店), 姐妹街边手提串串, 金地饭店餐厅
Restaurants around location 204: 叶麻辣(内曹家巷), 花蜀串串, 阿龙冷淡杯, 赵记烤鸭店(五昭路店), 虾餚, 福禧源大漠风情新疆风味餐馆(石油路店), 臻味坊, 杏花村(猛追湾街店)
Restaurants around location 205: 朱小妹烤五花(第五大道店), 哐吃社耗儿鱼(建设路店), 自贡芭夯兔(建设路店), 大反寿司, 抖食料理(建设路总店), 老三公益虾(建业路店), 成都市很好吃的火锅粉(建设巷总店), 鱼儿纸包鱼(建设路店)
Restaurants around location 206: 上半场冷锅串串, 沙河小院, 东郊酒馆, 重庆老灶王老火锅(东郊记忆店), 潘二姐兔丁(红枫岭店), 乐在鲜啤, Vitos泰式料理小酒馆, 朱烧烤特色烤全茄
Restaurants around location 207: 砂锅串串(理工店), 鸿源饭馆, 口口香川菜(长邻潭社区卫生站西北), 周记川菜稀饭庄, 胖妹火锅冒菜, 小狸冒菜干锅, 如忆美食坊, 香菇烤鸭
Restaurants around location 208: 承接农家乐火锅中餐厨房用具
Restaurants around location 209: 
Restaurants around location

Let's now see all the collected restaurants in our area of interest on map, and let's also show Hot Pot restaurants in different color.

In [74]:
map_ChengDu= folium.Map(location=chengdu_center_new, zoom_start=13)
folium.Marker(chengdu_center_new, popup='Tian Fu Square').add_to(map_ChengDu)
#print(chengdu_center_new)

for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_hot_pot = res[6]
    color = 'red' if is_hot_pot else 'blue'
    folium.CircleMarker([lat,lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_ChengDu)
    #folium.Circle([coordinate_WG84[1],coordinate_WG84[0]], radius=10, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_chengdu)
map_ChengDu



Looking good. So now we have all the restaurants in area within few kilometers from TianFu Square, and we know which ones are Hot Pot restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Hot Pot restaurant!


## Methodology <a name="methodology"></a>

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the number of restaurants in every area candidate

In [65]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 21.755494505494507


Address   formatted_address   Latitude   Longitude              X  \
0                   四川省成都市双流区  30.524351  104.014528  405454.853184   
1              四川省成都市双流区锦江路四段  30.524476  104.031203  407054.853184   
2              四川省成都市双流区滨河路2段  30.524599  104.047878  408654.853184   
3              四川省成都市双流区伏龙路1段  30.524720  104.064554  410254.853184   
4               四川省成都市双流区新通大道  30.524838  104.081229  411854.853184   
5               四川省成都市双流区新通大道  30.524955  104.097905  413454.853184   
6                四川省成都市双流区双简路  30.525069  104.114581  415054.853184   
7          四川省成都市双流区长城路2段-59号  30.536661  103.989386  403054.853184   
8                   四川省成都市双流区  30.536789  104.006063  404654.853184   
9                四川省成都市双流区荣店路  30.536916  104.022740  406254.853184   

              Y  Distance from center  Restaurants in area  
0  3.377303e+06          15979.987484                    8  
1  3.377303e+06          15574.337867                    0  
2  3.377303e+06          15325.795249                   17  
3  3.377303e+06          15242.047107                   91  
4  3.377303e+06          15325.795249                    2  
5  3.377303e+06          15574.337867                    0  
6  3.377303e+06          15979.987484                    0  
7  3.378689e+06          15615.377037                    0  
8  3.378689e+06          14945.233354                    0  
9  3.378689e+06          14422.205102                    0

In [66]:
distances_to_hot_pot_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in hot_pot_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_hot_pot_restaurant.append(min_distance)

df_locations['Distance to Hot Pot restaurant'] = distances_to_hot_pot_restaurant

In [67]:
df_locations.head(10)

Address   formatted_address   Latitude   Longitude              X  \
0                   四川省成都市双流区  30.524351  104.014528  405454.853184   
1              四川省成都市双流区锦江路四段  30.524476  104.031203  407054.853184   
2              四川省成都市双流区滨河路2段  30.524599  104.047878  408654.853184   
3              四川省成都市双流区伏龙路1段  30.524720  104.064554  410254.853184   
4               四川省成都市双流区新通大道  30.524838  104.081229  411854.853184   
5               四川省成都市双流区新通大道  30.524955  104.097905  413454.853184   
6                四川省成都市双流区双简路  30.525069  104.114581  415054.853184   
7          四川省成都市双流区长城路2段-59号  30.536661  103.989386  403054.853184   
8                   四川省成都市双流区  30.536789  104.006063  404654.853184   
9                四川省成都市双流区荣店路  30.536916  104.022740  406254.853184   

              Y  Distance from center  Restaurants in area  \
0  3.377303e+06          15979.987484                    8   
1  3.377303e+06          15574.337867                    0   
2  3.377303e+06          15325.795249                   17   
3  3.377303e+06          15242.047107                   91   
4  3.377303e+06          15325.795249                    2   
5  3.377303e+06          15574.337867                    0   
6  3.377303e+06          15979.987484                    0   
7  3.378689e+06          15615.377037                    0   
8  3.378689e+06          14945.233354                    0   
9  3.378689e+06          14422.205102                    0   

   Distance to Hot Pot restaurant  
0                     3388.639029  
1                     1815.296410  
2                      477.208179  
3                      373.190451  
4                     1080.333151  
5                     2671.231484  
6                     3429.724512  
7                     1937.303086  
8                     2169.230737  
9                     2431.864122

In [68]:
print('Average distance to closest Hot Pot restaurant from each area center:', df_locations['Distance to Hot Pot restaurant'].mean())

Average distance to closest Hot Pot restaurant from each area center: 1221.1517469906903


OK, so on average Hot Pot restaurant can be found **within ~1500m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

In [69]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

hot_pot_latlons = [[res[2], res[3]] for res in hot_pot_restaurants.values()]

In [72]:
from folium import plugins
from folium.plugins import HeatMap

map_chengdu = folium.Map(location=chengdu_center_new, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_chengdu) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_chengdu)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
folium.Circle(chengdu_center_new, radius=3000, fill=False, color='white').add_to(map_chengdu)
folium.Circle(chengdu_center_new, radius=10000, fill=False, color='white').add_to(map_chengdu)
folium.Circle(chengdu_center_new, radius=16000, fill=False, color='white').add_to(map_chengdu)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_chengdu

In [73]:
from folium import plugins
from folium.plugins import HeatMap

map_chengdu = folium.Map(location=chengdu_center_new, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_chengdu) #cartodbpositron cartodbdark_matter
HeatMap(hot_pot_latlons).add_to(map_chengdu)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
folium.Circle(chengdu_center_new, radius=3000, fill=False, color='white').add_to(map_chengdu)
folium.Circle(chengdu_center_new, radius=10000, fill=False, color='white').add_to(map_chengdu)
folium.Circle(chengdu_center_new, radius=16000, fill=False, color='white').add_to(map_chengdu)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_chengdu

高新南区是成都市未来发展的重心，有大量的人口，可以选择西北区域距离天府广场10KM附近，西南边具体天府广场附近10KM到16KM附近

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of South high-tech zone

In [80]:
roi_x_min = chengdu_center_x - 3000
roi_y_max = chengdu_center_y - 16000
roi_width = 8000
roi_height = 8000
roi_center_x = roi_x_min + 4000
roi_center_y = roi_y_max + 4000
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_chengdu = folium.Map(location=roi_center, zoom_start=13)
HeatMap(restaurant_latlons).add_to(map_chengdu)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
folium.Circle(roi_center, radius=4000, color='white', fill=True, fill_opacity=0.4).add_to(map_chengdu)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_chengdu

Not bad - this nicely covers all the pockets of low restaurant density in South high-tech zone

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 200m appart).

In [82]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 200
y_step = 200 * k 
roi_y_min = roi_center_y - 400

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(41/k)):
    y = roi_y_min + i * y_step
    x_offset = 100 if i%2==0 else 0
    for j in range(0, 41):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 4001):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

833 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: number of restaurants in vicinity (we'll use radius of 500 meters) and distance to closest Hot Pot restaurant

In [84]:
def count_restaurants_nearby(x, y, restaurants, radius=500):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_hot_pot_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=500)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, hot_pot_restaurants)
    roi_hot_pot_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [86]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Hot Pot restaurant':roi_hot_pot_distances})

df_roi_locations.head(30)

Latitude   Longitude              X             Y  Restaurants nearby  \
0   30.550142  104.034076  407354.853184  3.380145e+06                   0   
1   30.550157  104.036161  407554.853184  3.380145e+06                   0   
2   30.550173  104.038246  407754.853184  3.380145e+06                   2   
3   30.550188  104.040331  407954.853184  3.380145e+06                   2   
4   30.550203  104.042416  408154.853184  3.380145e+06                   2   
5   30.550219  104.044501  408354.853184  3.380145e+06                   4   
6   30.550234  104.046586  408554.853184  3.380145e+06                  11   
7   30.550249  104.048671  408754.853184  3.380145e+06                  17   
8   30.550264  104.050756  408954.853184  3.380145e+06                  24   
9   30.550280  104.052841  409154.853184  3.380145e+06                  24   
10  30.550295  104.054926  409354.853184  3.380145e+06                  17   
11  30.550310  104.057011  409554.853184  3.380145e+06                   8   
12  30.550325  104.059096  409754.853184  3.380145e+06                   6   
13  30.550340  104.061181  409954.853184  3.380145e+06                   4   
14  30.550355  104.063266  410154.853184  3.380145e+06                  33   
15  30.550370  104.065351  410354.853184  3.380145e+06                  45   
16  30.550385  104.067435  410554.853184  3.380145e+06                  46   
17  30.550400  104.069520  410754.853184  3.380145e+06                  28   
18  30.550415  104.071605  410954.853184  3.380145e+06                   6   
19  30.550430  104.073690  411154.853184  3.380145e+06                   6   
20  30.550444  104.075775  411354.853184  3.380145e+06                  11   
21  30.550459  104.077860  411554.853184  3.380145e+06                  10   
22  30.550474  104.079945  411754.853184  3.380145e+06                   9   
23  30.550489  104.082030  411954.853184  3.380145e+06                   4   
24  30.550503  104.084115  412154.853184  3.380145e+06                   3   
25  30.550518  104.086200  412354.853184  3.380145e+06                   0   
26  30.550532  104.088285  412554.853184  3.380145e+06                   1   
27  30.550547  104.090370  412754.853184  3.380145e+06                   6   
28  30.550562  104.092455  412954.853184  3.380145e+06                   7   
29  30.550576  104.094540  413154.853184  3.380145e+06                  10   

    Distance to Hot Pot restaurant  
0                      1100.503398  
1                      1049.830584  
2                      1035.944391  
3                      1060.291143  
4                      1120.381111  
5                      1210.904769  
6                      1325.642066  
7                      1405.123215  
8                      1239.186899  
9                      1084.802789  
10                      947.633902  
11                      810.185250  
12                      630.186232  
13                      466.764647  
14                      344.389001  
15                      315.179840  
16                      352.068601  
17                      395.699305  
18                      300.884927  
19                      145.750963  
20                      178.759468  
21                      350.237850  
22                      541.643938  
23                      737.624403  
24                      935.308165  
25                     1073.180403  
26                     1214.537978  
27                     1219.466148  
28                     1032.015830  
29                      850.303275

OK. Let us now filter those locations: we're interested only in locations with no more than 5 restaurants in radius of 500 meters, and no Italian restaurants in radius of 1200 meters.

In [94]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=10))
print('Locations with no more than ten restaurants nearby:', good_res_count.sum())

good_hot_pot_distance = np.array(df_roi_locations['Distance to Hot Pot restaurant']>=1000)
print('Locations with no Italian restaurants within 1200m:', good_hot_pot_distance.sum())

good_locations = np.logical_and(good_res_count, good_hot_pot_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than ten restaurants nearby: 516
Locations with no Italian restaurants within 1200m: 304
Locations with both conditions met: 258


Let's see how this looks on a map.

In [95]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_chengdu = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_chengdu)
HeatMap(restaurant_latlons).add_to(map_chengdu)
folium.Circle(roi_center, radius=4000, color='white', fill=True, fill_opacity=0.6).add_to(map_chengdu)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_chengdu) 
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_chengdu)
map_chengdu

Looking good. We now have a bunch of locations fairly close to Alexanderplatz (mostly in Kreuzberg, Friedrichshain and south-east corner of Mitte boroughs), and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [97]:
map_chengdu = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_chengdu)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_chengdu)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_chengdu)
map_chengdu

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and no Hot Pot restaurants at all nearby.

Let us now cluster those locations to create centers of zones containing good locations. Those zones, their centers and addresses will be the final result of our analysis.


In [100]:
from sklearn.cluster import KMeans

number_of_clusters = 8

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_chengdu = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_chengdu)
HeatMap(restaurant_latlons).add_to(map_chengdu)
folium.Circle(roi_center, radius=4000, color='white', fill=True, fill_opacity=0.4).add_to(map_chengdu)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_chengdu) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_chengdu)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_chengdu



Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:


In [102]:
map_chengdu = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=500, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_chengdu)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_chengdu)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=1000, color='green', fill=False).add_to(map_chengdu) 
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_chengdu)
map_chengdu

In [107]:
map_chengdu = folium.Map(location=[30.577022, 104.092826], zoom_start=15)
folium.Marker(chengdu_center_new).add_to(map_chengdu)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=1000, color='green', fill=False).add_to(map_chengdu) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=500, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_chengdu)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_chengdu)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_chengdu

In [106]:

#http://api.map.baidu.com/place/v2/search?query=ATM机&tag=银行&region=北京&output=json&ak=您的ak //GET请求
address='优固美家私'
def get_coordinates(token,address):
    try:
        url = 'http://api.map.baidu.com/place/v2/search?query='+address+'&region=成都&output=json&ak='+token#+'&callback=showLocation'
        print(url)
        r = requests.get(url)
        #print(r)
        #r = requests.post(url)
        response_dict = r.json()
        #print(response_dict)
        results = response_dict['results']
        results_first =  results[0] #get address details fet the first row
        #print(results_first)
        coordinate = results_first['location']
        province = results_first['province']
        city = results_first['city']
        area = results_first['area']
        addressdetails = results_first['address']
        lng=coordinate['lng']
        lat=coordinate['lat']
        return [lat, lng]
    except:
        return[None,None]        
xxdf = get_coordinates(token,address)
print('Coordinate of {}: {}'.format(address, xxdf))

http://api.map.baidu.com/place/v2/search?query=优固美家私&region=成都&output=json&ak=n6iyUTUq8aUBflLOgfz7wZpEjzccNagj
Coordinate of 优固美家私: [30.577022, 104.092826]


Finaly, let's reverse geocode those candidate area centers to get the addresses which can be presented to stakeholders.

In [112]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr,formatted_address = get_address(lat, lon,coordtype = 'wgs84ll',ret_coordtype = 'wgs84ll' )
    candidate_area_addresses.append(formatted_address)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, chengdu_center_x, chengdu_center_y)
    print('{}{} => {:.1f}km from TianFuSquare'.format(formatted_address, ' '*(50-len(addr)), d/1000))


Addresses of centers of areas recommended for further analysis

四川省成都市武侯区锦悦西路                                             => 9.8km from TianFuSquare
四川省成都市锦江区康达路                                           => 9.9km from TianFuSquare
四川省成都市锦江区                                              => 8.9km from TianFuSquare
四川省成都市锦江区琉新路                                                 => 12.4km from TianFuSquare
四川省成都市武侯区荣华南路                                               => 12.6km from TianFuSquare
四川省成都市双流区中和大道62号                                           => 12.4km from TianFuSquare
四川省成都市锦江区G4202(成都绕城高速)                                           => 10.2km from TianFuSquare
四川省成都市双流区江家立交                                                 => 10.9km from TianFuSquare


This concludes our analysis. We have created 8 addresses representing centers of zones containing locations with low number of restaurants and no Hot Pot restaurants nearby, all zones being fairly close to high-tech district center . Although zones are shown on map with a radius of ~1000 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in high-tech district , which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [114]:
map_chengdu = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(chengdu_center_new, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_chengdu)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_chengdu) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=500, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_chengdu)
map_chengdu

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in ChengDu (~There are nearly 10,000 restaurants within a 16-kilometer radius of tianfu square), there are pockets of low restaurant density fairly close to high-tech district center. Highest concentration of restaurants was detected north and south west from TianFu square, so we focused our attention to areas south(high-tech district center),which offer a combination of strong socio-economic dynamics and a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 8x8km from TianFu square) we first created a dense grid of location candidates (spaced 200m appart); those locations were then filtered so that those with more than ten restaurants in radius of 500m and those with an Hot Pot restaurant closer than 1000m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using baidu api to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 8 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Hot Pot restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas  not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify ChengDu areas close to center with low number of restaurants (particularly Hot Pot restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Hot Pot restaurant. By calculating restaurant density distribution from BaiDu data we have first identified general boroughs that justify further analysis (high-tech district), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.
